In [ ]:
!pip3 install tinkoff-investments
!pip3 install yfinance
!pip3 install pandas
!pip3 install numpy
!pip3 install decimal
!pip3 install locale

In [146]:
from tinkoff.invest import Client

TOKEN = 't.b7eKSJEp3fpSiiv4mVt4fWwKIxaMHM1lDMtpGsPTeyl850b9Y4MluXYv-EQrj1vEu7QfkNwqGqGPfTW9N6EvTg'

import pandas as pd
import numpy as np
from datetime import timedelta
from pathlib import Path
from datetime import datetime, timedelta, timezone
from decimal import Decimal
from tinkoff.invest import CandleInterval, Client, HistoricCandle, Quotation, SubscriptionInterval
from tinkoff.invest.caching.market_data_cache.cache_settings import (
    MarketDataCacheSettings,
)
from tinkoff.invest.services import MarketDataCache
from tinkoff.invest.utils import now

__all__ = (
    "get_intervals",
    "quotation_to_decimal",
    "decimal_to_quotation",
    "candle_interval_to_subscription_interval",
    "now",
    "candle_interval_to_timedelta",
    "ceil_datetime",
    "floor_datetime",
    "dataclass_from_dict",
    "datetime_range_floor",
)


'''MoneyValue — используется для параметров, у которых есть денежный эквивалент. Возьмем для примера стоимость ценных бумаг — тип состоит из трех параметров:
1) currency — строковый ISO-код валюты, например RUB или USD;
2) units — целая часть суммы;
3) nano — дробная часть суммы, миллиардные доли единицы.
'''
# Quotation type = MoneyValue. We need to convert this to decimal in order to fetch price per share
def quotation_to_decimal(quotation: Quotation) -> Decimal:
    fractional = quotation.nano / Decimal("10e8")
    return Decimal(quotation.units) + fractional

def get_final_stock_volumes(_input: int):
    return f'Объем: {_input:,} ₽'

def get_final_lots(_lots: int):
    return f'Кол-во лотов: {_lots:,} шт.'

volumes = []
prices = []

def main():
    with Client(TOKEN) as client:
        settings = MarketDataCacheSettings(base_cache_dir=Path("market_data_cache"))
        market_data_cache = MarketDataCache(settings=settings, services=client)
        for candle in market_data_cache.get_all_candles(
            figi="BBG004731032",
            from_=now() - timedelta(days=90),
            interval=CandleInterval.CANDLE_INTERVAL_1_MIN,
        ):
            final_stock_volume_rub = int(candle.volume * quotation_to_decimal(candle.close))
            volumes.append(final_stock_volume_rub)
            prices.append(int(quotation_to_decimal(candle.close)))
            print(f'Лукойл (LKOH), Время: {candle.time}, {get_final_lots(candle.volume)}, {get_final_stock_volumes(final_stock_volume_rub)}, Цена: {quotation_to_decimal(candle.close)} ₽')
        
    return 0

if __name__ == "__main__":
    main()
    print(volumes)
    print(prices)


Лукойл (LKOH), Время: 2023-02-10 11:26:00+00:00, Кол-во лотов: 88 шт., Объем: 344,168 ₽, Цена: 3911.00000000 ₽
Лукойл (LKOH), Время: 2023-02-10 11:27:00+00:00, Кол-во лотов: 71 шт., Объем: 277,681 ₽, Цена: 3911.00000000 ₽
Лукойл (LKOH), Время: 2023-02-10 11:28:00+00:00, Кол-во лотов: 108 шт., Объем: 422,496 ₽, Цена: 3912.00000000 ₽
Лукойл (LKOH), Время: 2023-02-10 11:29:00+00:00, Кол-во лотов: 147 шт., Объем: 575,064 ₽, Цена: 3912.00000000 ₽
Лукойл (LKOH), Время: 2023-02-10 11:30:00+00:00, Кол-во лотов: 130 шт., Объем: 508,560 ₽, Цена: 3912.00000000 ₽
Лукойл (LKOH), Время: 2023-02-10 11:31:00+00:00, Кол-во лотов: 833 шт., Объем: 3,259,112 ₽, Цена: 3912.50000000 ₽
Лукойл (LKOH), Время: 2023-02-10 11:32:00+00:00, Кол-во лотов: 434 шт., Объем: 1,699,544 ₽, Цена: 3916.00000000 ₽
Лукойл (LKOH), Время: 2023-02-10 11:33:00+00:00, Кол-во лотов: 127 шт., Объем: 497,586 ₽, Цена: 3918.00000000 ₽
Лукойл (LKOH), Время: 2023-02-10 11:34:00+00:00, Кол-во лотов: 583 шт., Объем: 2,284,194 ₽, Цена: 3918

In [109]:
import numpy as np
data = {'Объем': volumes}
df = pd.DataFrame(data)

volume_threshold = 0.9975  # 99.75%
price_change_threshold = 0.9975  # 99.75%

for volume in range(len(df)):
    volume_mean_past_90_days = df['Объем'].mean()
    # Calculate the volume threshold
    volume_threshold_value = np.quantile(volume_mean_past_90_days, volume_threshold)
    if df['Объем'].iloc[volume] > volume_threshold_value:
        print(f'Зафиксирован аномальный объем: {get_final_stock_volumes(df["Объем"].iloc[volume])}')


Зафиксирован аномальный объем: Объем: 3,745,301 ₽
Зафиксирован аномальный объем: Объем: 3,722,320 ₽
Зафиксирован аномальный объем: Объем: 8,112,451 ₽
Зафиксирован аномальный объем: Объем: 5,739,390 ₽
Зафиксирован аномальный объем: Объем: 9,346,632 ₽
Зафиксирован аномальный объем: Объем: 3,999,930 ₽
Зафиксирован аномальный объем: Объем: 4,678,752 ₽
Зафиксирован аномальный объем: Объем: 5,568,187 ₽
Зафиксирован аномальный объем: Объем: 4,145,857 ₽
Зафиксирован аномальный объем: Объем: 3,235,824 ₽
Зафиксирован аномальный объем: Объем: 5,508,165 ₽
Зафиксирован аномальный объем: Объем: 5,539,417 ₽
Зафиксирован аномальный объем: Объем: 3,569,373 ₽
Зафиксирован аномальный объем: Объем: 6,264,621 ₽
Зафиксирован аномальный объем: Объем: 4,243,318 ₽
Зафиксирован аномальный объем: Объем: 13,747,320 ₽
Зафиксирован аномальный объем: Объем: 14,674,230 ₽
Зафиксирован аномальный объем: Объем: 3,858,183 ₽
Зафиксирован аномальный объем: Объем: 3,207,020 ₽
Зафиксирован аномальный объем: Объем: 3,259,112 

In [23]:
def get_final_stock_volumes(_input):
    return f'Объем: {_input:,} ₽'

def get_final_lots(_lots):
    return f'Кол-во лотов: {_lots:,} шт.'


price = 4666.00000000
lots = 1085
print(f'Цена: {price} ₽')
print(get_final_lots(lots))
output = int(price * lots)
print(output)
print(get_final_stock_volumes(output))


Цена: 4666.0 ₽
Кол-во лотов: 1,085 шт.
5062610
Объем: 5,062,610 ₽


In [147]:
#data = {'Время': ['2023-05-10 13:52:00+00:00', '2023-05-10 13:52:00+00:00'], 'Кол-во лотов': [380, 832852], 'Объем': [2134324, 23455], 'Цена': [4647.00000000, 4645.50000000]}
data = {'Объем': volumes, 'Цена': prices}
df = pd.DataFrame(data)
threshold = 5.0

# Calculate the rolling average and standard deviation of the trading volume
volume_mean = round(df['Объем'].mean())
volume_std = round(df['Объем'].std())

# Calculate the rolling average and standard deviation of the trading prices
prcies_mean = round(df['Цена'].mean())
prices_std = round(df['Цена'].std())

#abnormal_volume = (df['Объем'].iloc[-1] - volume_mean) / volume_std

def calculate_net_change(current_closing_price: int, prev_closing_price: int):
    return f'Изменение цены: {(current_closing_price - prev_closing_price) / prev_closing_price * 100}'


for i in range(len(df)):
    abnormal_volume = (df['Объем'].iloc[i] - volume_mean) / volume_std
    abnormal_price_changes = (df['Цена'].iloc[i] - prcies_mean) / prices_std
    #print(abnormal_volume, abnormal_price_changes)

    if abnormal_volume > threshold or abnormal_price_changes > threshold:
        print(f'Зафиксирован аномальный объем: {get_final_stock_volumes(df["Объем"].iloc[i])},  Цена: {df["Цена"].iloc[i]} ₽, {calculate_net_change(df["Цена"].iloc[i], df["Цена"].iloc[i - 1])}')



Зафиксирован аномальный объем: Объем: 164,369,712 ₽,  Цена: 3856 ₽, Изменение цены: -1.481859989780276
Зафиксирован аномальный объем: Объем: 69,422,050 ₽,  Цена: 3852 ₽, Изменение цены: -0.12963443090484833
Зафиксирован аномальный объем: Объем: 63,894,580 ₽,  Цена: 3860 ₽, Изменение цены: 0.0
Зафиксирован аномальный объем: Объем: 90,500,256 ₽,  Цена: 3811 ₽, Изменение цены: -0.8842652795838752
Зафиксирован аномальный объем: Объем: 82,748,068 ₽,  Цена: 3904 ₽, Изменение цены: 0.1796253528355145
Зафиксирован аномальный объем: Объем: 54,332,370 ₽,  Цена: 3915 ₽, Изменение цены: 0.02554931016862545
Зафиксирован аномальный объем: Объем: 65,519,041 ₽,  Цена: 3973 ₽, Изменение цены: 0.17650025214321735
Зафиксирован аномальный объем: Объем: 62,432,579 ₽,  Цена: 3998 ₽, Изменение цены: 0.10015022533800699
Зафиксирован аномальный объем: Объем: 70,510,440 ₽,  Цена: 4004 ₽, Изменение цены: 0.12503125781445362
Зафиксирован аномальный объем: Объем: 52,626,840 ₽,  Цена: 3999 ₽, Изменение цены: -0.149